In [1]:
# 1. Install required libraries
!pip install --upgrade openai pandas openpyxl

# 2. Import Python libraries
import os
import zipfile
import base64
import pandas as pd
import re
from openai import OpenAI
from google.colab import files

# 3. Load OpenAI API key from Colab secret storage (or environment variable)
from google.colab import userdata
api_key = userdata.get('OPENAI_API_KEY')  # The key should be stored under this name
client = OpenAI(api_key=api_key)

# 4. Unzip the uploaded ZIP archive containing the images
zip_path = "/content/strawberry_class.zip"
extract_path = "/content/images"
os.makedirs(extract_path, exist_ok=True)

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_path)

# 5. Get list of image files in the extracted folder
image_files = [f for f in os.listdir(extract_path) if f.lower().endswith(('.jpg', '.jpeg', '.png'))]

# 6. Classify each image using GPT-4o and keep only the word 'fresh' or 'scorch'
results = []

for filename in sorted(image_files):  # Optional: sort alphabetically for consistent output
    image_path = os.path.join(extract_path, filename)

    with open(image_path, "rb") as img_file:
        image_data = img_file.read()
        b64_image = base64.b64encode(image_data).decode("utf-8")

    response = client.chat.completions.create(
        model="gpt-4o",
        messages=[
            {"role": "system", "content": "You are a plant pathology expert."},
            {
                "role": "user",
                "content": [
                    {"type": "text", "text": "Classify this strawberry leaf as either 'fresh' or 'scorch'. Reply with only one word: fresh or scorch."},
                    {"type": "image_url", "image_url": {"url": f"data:image/jpeg;base64,{b64_image}"}}
                ]
            }
        ],
        max_tokens=5
    )

    # Extract only 'fresh' or 'scorch' from the response (strict match)
    text = response.choices[0].message.content.lower()
    match = re.search(r'\b(fresh|scorch)\b', text)
    classification = match.group(1) if match else ""

    results.append({"Filename": filename, "Classification": classification})

# 7. Save results to Excel file
df = pd.DataFrame(results)
excel_path = "/content/strawberry_leaf_classification.xlsx"
df.to_excel(excel_path, index=False)

# 8. Download Excel file
files.download(excel_path)


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.9/89.9 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 720.4/720.4 kB 15.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 76.1 MB/s eta 0:00:00
  Attempting uninstall: pandas
    Found existing installation: pandas 2.2.2
    Uninstalling pandas-2.2.2:
      Successfully uninstalled pandas-2.2.2
  Attempting uninstall: openai
    Found existing installation: openai 1.81.0
    Uninstalling openai-1.81.0:
      Successfully uninstalled openai-1.81.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires pandas==2.2.2, but you have pandas 2.2.3 which is incompatible.


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>